# 第一步，爬取金融学院网站获取所有硕士生导师的URL

In [2]:
import requests
from lxml import etree

# 获得所有教师链接信息
namesUrl = []
for i in range(1,4):
    html = requests.get("http://finance.jxufe.edu.cn/news-list-shuodao-%d.html"%i)
    text = etree.HTML(html.text)
    li = text.xpath("//html/body/div[1]/div[2]/div[2]/div[2]/div/ul/li/div/a/@href")
    # 去重并合并列表
    li = li[::2]
    namesUrl += list(li)

# 第二步，爬取每个硕导URL里的信息

In [7]:
import re
# 创建存储数据的变量
dicts = {'姓名':[],
         '性别':[],
         '出生年月':[],
         '政治面貌':[],
         '毕业院校':[],
         '毕业专业':[],
         '职务':[],
         '职称':[],
         '邮箱':[],
         '自我简介':[],
         '科研成果':[]
        }
count = 0
# 获取信息
for url in namesUrl:
    # 获取第一种数据
    html = requests.get(url)
    text = etree.HTML(html.text)
    # 基本信息
    xinxi = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[1]/p/text()")
    
    temp = []
    for i in xinxi:
        i = i.split("：")
        if len(i) == 2:
            temp.append(i[-1])
    xinxi = temp
    # 等于10 说明基本信息缺失
    if len(xinxi) == 8:
        xinxi.append("")
    
    # 自我简介+科研成功
    res = re.findall(r'<div class="jianjie_c">(.*?)</div>',html.text)
    if len(res) == 2:
        dr = re.compile(r'<[^>]+>',re.S)
        dd = dr.sub('',res[0])
        xinxi.append(dd)
        
        dr = re.compile(r'<[^>]+>',re.S)
        dd = dr.sub('',res[1])
        xinxi.append(dd)
    # 如果获取信息数量正确
    if len(xinxi) == 11:
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
    # 补充缺失数据
    if count == 0:
        xinxi = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td/p/span/text()")
        temp = []
        for i in xinxi:
            temp.append(i.split(": ")[-1])
        xinxi = temp
        email = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td/p[6]/span/a/span/text()")
        txt = []
        for index in range(20,80):
            txt += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/span/text()"%index)
        dicts['姓名'].append(xinxi[0])
        dicts['性别'].append(xinxi[1])
        dicts['出生年月'].append('')
        dicts['政治面貌'].append('')
        dicts['毕业院校'].append(xinxi[3])
        dicts['毕业专业'].append('')
        dicts['职务'].append(xinxi[4])
        dicts['职称'].append(xinxi[2])
        dicts['邮箱'].append(email)
        dicts['自我简介'].append('')
        dicts['科研成果'].append(" ".join(txt))
    if count == 5:
        xinxi = []
        for index in range(2,11):
            xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/text()"%index)
        xinxi = [x.strip("：") for x in xinxi]
        jianjie = [] 
        jianjie += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[13]/span/text()")
        jianjie += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[14]/span/text()")
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
            if len(xinxi) == index:
                break
        dicts['自我简介'].append(''.join(jianjie))
        dicts['科研成果'].append("")
    if count == 9 or count == 20 or count == 23: 
        xinxi = []
        for index in range(2,11): #
            if count == 9:
                xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/span/text()"%index)
            if count == 20 or count == 23:
                xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/text()"%index)
        xinxi = [x.strip("：") for x in xinxi]
        chengguo = []
        for index in range(35,60):
            chengguo += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/span/text()"%index)
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
            if len(xinxi) == index:
                break
        dicts['自我简介'].append("")
        dicts['科研成果'].append(''.join(chengguo))
    if count == 14 or count == 18:
        xinxi = []
        xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p/span[1]/text()")
        for index in range(1,9):
            if count == 14:
                xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[1]/p[%d]/span/text()"%index)
            if count == 18: 
                xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[1]/p[%d]/span/text()"%index)
        if count == 18: 
            xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[1]/p[9]/span/span/text()")
        xinxi = [x.strip("：") for x in xinxi]
        jianjie = [] # 
        jianjie += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[2]/p[4]/span/text()")
        chengguo = []
        for index in range(11,53):
            chengguo += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/div[2]/p[%d]/span/span/text()"%index)
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
            if len(xinxi) == index:
                break
        dicts['自我简介'].append("".join(jianjie))
        dicts['科研成果'].append(''.join(chengguo))
    if count == 16 or count == 31: 
        xinxi = [] 
        for index in range(3,11): 
            if count == 16:
                xinxi += text.xpath("//html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/span/text()"%index)
            if count == 31:
                xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[%d]/span/text()"%index)
        xinxi = [x.strip("：") for x in xinxi]
        if count == 16:
            xinxi.append("")
            xinxi.append("")
        if count == 31:
            xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/p[11]/span/text()")
            xinxi.pop(2)
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
            if len(xinxi) == index:
                break
        dicts['自我简介'].append("")
        dicts['科研成果'].append('')
    if count == 25:
        name = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[1]/span/span[1]/text()")[0]
        sex = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[2]/span[2]/text()")[0]
        bri = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[3]/span/span/text()")
        bri = "".join(bri)
        xl = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[4]/span/text()")
        sc = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[5]/span[1]/text()")
        zc = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[7]/span/text()")
        zc = "".join(zc)
        email = text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td[1]/p[6]/span[2]/a/span/text()")
        dicts['姓名'].append(name)
        dicts['性别'].append(sex)
        dicts['出生年月'].append(bri)
        dicts['政治面貌'].append('')
        dicts['毕业院校'].append(sc)
        dicts['毕业专业'].append(xl)
        dicts['职务'].append("")
        dicts['职称'].append(zc)
        dicts['邮箱'].append(email)
        dicts['自我简介'].append('')
        dicts['科研成果'].append("")
    if count == 28:
        xinxi = [] 
        for index in range(1,7): 
            xinxi += text.xpath("/html/body/div[1]/div[2]/div[2]/div[2]/table/tbody/tr/td/p[%d]/span/text()"%index)
        xinxi = [x.split("：")[-1] for x in xinxi]
        xinxi.insert(2,"")
        xinxi.insert(5,"")
        xinxi.insert(7,"")
        print(xinxi)
        xinxi = [x.strip("：") for x in xinxi]
        index = 0
        for key in dicts:
            dicts[key].append(xinxi[index])
            index += 1
            if len(xinxi) == index:
                break
        dicts['自我简介'].append("")
        dicts['科研成果'].append('')
    count += 1

['赵玉洁', '女', '', '1984', '复旦大学', '', '副教授', '', 'verg0601@126.com']


In [8]:
from IPython.display import display, HTML
from pandas import DataFrame
df = DataFrame(dicts)
print("df:")
display(df)

df:


姓名    性别     出生年月     政治面貌  \
0   Badar Nadeem Ashraf  Male                     
1                    曹邓     女              中共党员   
2                   陈春霞     女                群众   
3                   陈家洪     男              中共党员   
4                   冯凌秉     男                     
5                   桂荷发     男              民进会员   
6                   胡少勇     男              中共党员   
7                   胡援成     男                党员   
8                   胡志军     男              中共党员   
9                   蒋崇辉     男   1980.9     中共党员   
10                  李思敏     男              中共党员   
11                  刘金凤     女                     
12                  刘兴华     男              中共党员   
13                  吕江林     男              中共党员   
14                  闵晓平     男  1974年7月  中国民主促进会   
15                  钱建豪     男                     
16                   潜力     男                     
17                   寿晖     男                     
18                  舒海棠     女  1969.11     中共党员   
19                  孙爱琳     女              中共党员   
20                   汪洋     男              中共党员   
21                   王辉     男              中共党员   
22                  王清生     男                群众   
23                  吴伟军     男              中共党员   
24                   严武     男                党员   
25                   杨超    男   1986年08            
26                   杨荣     女              中共党员   
27                  杨玉凤     女              民主党派   
28                  赵玉洁     女              1984   
29                  邹朋飞     男                群众   
30                  曾鸿志     男                党员   
31                  王金佑     男                     

                                             毕业院校             毕业专业  \
0   Huazhong University of Science and Technology                    
1                                          江西财经大学              管理学   
2                                          江西财经大学              金融学   
3                                          江西财经大学     经济统计（证券研究方向）   
4                                        澳大利亚国立大学              统计学   
5                                          中国人民大学              金融学   
6                                          华东师范大学              精算学   
7                                            厦门大学              金融学   
8                                          上海财经大学            数量经济学   
9                                          电子科技大学  管理科学与工程（金融工程方向）   
10                                                                   
11                                                                   
12                                           厦门大学             世界经济   
13                                         中南财经大学              经济学   
14                                         上海交通大学          管理科学与工程   
15                                                           经济学博士   
16                                         西安交通大学              金融学   
17                                                                   
18                                         江西财经大学              金融学   
19                                           浙江大学            政治经济学   
20                                         上海财经大学              金融学   
21                                         江西财经大学              财政学   
22                                           云南大学         概率论与数理统计   
23                                         江西财经大学              经济学   
24                                         江西财经大学              经济学   
25                                       [西南财经大学]             [博士]   
26                                         江西财经大学              金融学   
27                                         江西财经大学              金融学   
28                                           复旦大学                    
29                                           暨南大学              金融学   
30                                           天津大学          投资经济管理学   
31                                         中国人民大学            经济学硕士   

                          